# Обучение FastText

В бейзлайне предполагается использовать векторы из библиотеки FastText, которые в данном ноутбуке обучатся на домен чеков

In [1]:
from gensim.models.fasttext import FastText
import pandas as pd
import numpy as np

Выгрузим все чеки из размеченного датасета для обучения, а также из тестового датасета

In [2]:
train_df = pd.read_csv("data/train_supervised_dataset.csv").fillna("")
uns_train_df = pd.read_csv("data/train_unsupervised_dataset.csv").fillna("")
test_df = pd.read_csv("data/test_dataset.csv")
names = pd.concat((train_df[["name"]], test_df, uns_train_df[["name"]])).reset_index(drop=True)
names

name  id
0                  Petmax Бантик леопард с красн розой 2шт NaN
1                         87191 Бусы для елки шарики_87191 NaN
2                       Футболка Piazza Italia WR011446881 NaN
3           7) YI572-03X-ONE ЗАКОЛКА ДЛЯ ВОЛОС ДЛЯ ДЕВОЧКИ NaN
4                                        Одежда (вес) 1500 NaN
...                                                    ...  ..
1029995              F-2296  Спонж д/макияжа фигурный (шт) NaN
1029996               4 5702737510597 69.88 Дифф/Arom/1601 NaN
1029997  Матрас надувной 540*74см Tropical Bird запл.д/... NaN
1029998  пододеяльник СТМ Страйп 3-сп, размер: 796х185с... NaN
1029999  Пакет ламинированный вертикальный ?Чудесных мг... NaN

[1030000 rows x 2 columns]

In [23]:
import re

from cyrtranslit import to_cyrillic, to_latin
lat_to_cyr = str.maketrans("aekmhopctyx", "аекмнорстух")
cyr_to_lat = str.maketrans("аекмнорстух", "aekmhopctyx")
stop_words = set(['г', 'кг', 'шт', 'мл', 'л', 'литр', 'мг', 'гр', 'км', 'мм', 'mm', 'уп', 'скидка', 'цена'])

def replace_camel_case(s):
    matches = len(re.findall(r'(?<=[a-zа-я])([A-ZА-Я])', s))
    if matches > 2:
        return re.sub(r'(?<=[a-zа-я])([A-ZА-Я])', r' \1', s)
    else:
        return s
    

def split_on_language_change(s):
    s = re.sub(r'(?<=[a-zа-я])(?=[A-ZА-Я0-9])', r' ', s)
    s = re.sub(r'(?<=[A-ZА-Я0-9])(?=[a-zа-я])', r' ', s)
    return s


def insert_space_after_one(s):
    return re.sub(r'(1)(?=[A-Za-zА-Яа-я])', r'\1 ', s)

def replace_zero(s):
    s = re.sub(r'(?<=[A-Za-z])0(?=[A-Za-z])', 'o', s)
    s = re.sub(r'(?<=[А-Яа-я])0(?=[А-Яа-я])', 'о', s)
    return s

def preprocess_text(text):
    
    text = replace_zero(text)
    
    text = re.sub('\d+', '1', text)  # replace numbers to 1
    text = replace_camel_case(text)
    text = re.sub('д/', 'для ', text)
    text = re.sub('Д/', 'для ', text)
    text = insert_space_after_one(text)
    text = re.sub(r'\s+', ' ', text)  # remove extra spaces
    text = re.sub(r'[^\w\s]', ' ', text)  # remove punctuation
    words = []
    for w in text.lower().split():
#         if len(w) < 2:
#             continue
        
        num_eng_chars = len(re.findall(r'[a-z]', w))
        num_ru_chars = len(re.findall(r'[а-я]', w))
        if num_eng_chars and num_ru_chars:
            if num_eng_chars > num_ru_chars:
                w = w.translate(cyr_to_lat)
            else:
                w = w.translate(lat_to_cyr)
        
        if w in stop_words:
            continue
        
        # если нет транзиторов
        w = split_on_language_change(w)
        if ' ' in w:
            words.extend(w.split())
        else:
            if w == 'нести':
                w = 'nestea'
            if w == 'эпика':
                w = 'epica'
            if w == 'хелен':
                w = 'helen'
            if w == 'харпер':
                w = 'harper'
            if w == 'тимотей':
                w = 'timotei'
            if w == 'тесс':
                w = 'tess'
            if w == 'кроненбург':
                w = 'kronenbourg'
            if w == 'пай':
                w = 'pie'
            if w == 'чоко':
                w = 'choko'
            if w == 'салтон':
                w = 'salton'
            if w == 'винстон':
                w = 'winston'
            if w == 'липтон':
                w = 'lipton'
            if w == 'махеев':
                w = 'махеевъ'
            if w == 'яшкинская':
                w = 'яшкино'
            if w == 'редбулл':
                words.append('red')
                w = 'bull'
            words.append(w)
    return words

In [35]:
text = train_df['name'].sample().values[0]
text

'Вино Маркиз де Виллануева кр п/сл 0,75л Испания'

In [36]:
train_df[train_df['name'] == text]

id                                             name  good  \
17398  17398  Вино Маркиз де Виллануева кр п/сл 0,75л Испания  вино   

                       brand  \
17398  marques de villanueva   

                                               processed  num_spaces  
17398  [вино, маркиз, де, виллануева, кр, п, сл, 1, 1...           8

In [40]:
train_df[train_df['brand'] == 'ранкоф']

Empty DataFrame
Columns: [id, name, good, brand, processed, num_spaces]
Index: []

In [38]:
to_latin('Маркиз де Виллануева')

'Markiz de Villanueva'

In [26]:
%%timeit
preprocess_text(text)

54.7 µs ± 960 ns per loop (mean ± std. dev. of 7 runs, 10,000 loops each)


In [27]:
train_df['processed'] = train_df['name'].apply(lambda s: preprocess_text(s))

In [28]:
good_founded_list = []
brand_founded_list = []
DEBUG = True

complex_idx = []
for i, r in train_df.iterrows():
    tokens = preprocess_text(r['name'])
    brand = r['brand']
    good = r['good']
#     if len(re.findall(r'[a-z]', brand)) > 0 and brand not in tokens:
#         DEBUG = False
#     else:
#         DEBUG = False
    if DEBUG:
        print(r['name'])
    if brand:
        if DEBUG:
            print(f"brand: {brand}")
        brand_parts = brand.split()
        is_brand_found = all([part in tokens for part in brand.split()])
        brand_founded_list.append(is_brand_found)
        if not is_brand_found:
            complex_idx.append(i)
    if good:
        if DEBUG:
            print(f"good: {good}")
        good_founded_list.append(good in tokens)
    if DEBUG:
        print(tokens)
        print(f'\n\n')

Petmax Бантик леопард с красн розой 2шт
brand: petmax
good: бантик
['petmax', 'бантик', 'леопард', 'с', 'красн', 'розой', '1']



87191 Бусы для елки шарики_87191
good: бусы
['1', 'бусы', 'для', 'елки', 'шарики_1']



Футболка Piazza Italia WR011446881
brand: piazza italia
good: футболка
['футболка', 'piazza', 'italia', 'wr', '1']



7) YI572-03X-ONE ЗАКОЛКА ДЛЯ ВОЛОС ДЛЯ ДЕВОЧКИ
good: заколка
['1', 'yi', '1', '1', 'x', 'one', 'заколка', 'для', 'волос', 'для', 'девочки']



Одежда (вес) 1500
good: одежда
['одежда', 'вес', '1']



РУСАЛОЧКА Губка ТРИО трехслой.3 шт ЛЮКС
brand: русалочка
good: губка
['русалочка', 'губка', 'трио', 'трехслой', '1', 'люкс']



29-003 ОБОИ/ART/п.п. белые на флизе 1,06*10/островки/9//52
good: обои
['1', '1', 'обои', 'art', 'п', 'п', 'белые', 'на', 'флизе', '1', '1', '1', 'островки', '1', '1']



Квас Очаковский Пряная зима 2л
brand: очаковский
good: квас
['квас', 'очаковский', 'пряная', 'зима', '1']



14 2456549180228 НБ маска+п/COSY/М-Ив
brand: cosy
good: м

3.101033  Изолента синяя 19мм*25м Safeline 1шт 110,00* 10,000= 1100,00 р./арт.88576      Со скидкой: 110,00* 10,000= 1100,00 р.
brand: safeline
good: изолента
['1', '1', 'изолента', 'синяя', '1', '1', 'м', 'safeline', '1', '1', '1', '1', '1', '1', '1', 'р', 'арт', '1', 'со', 'скидкой', '1', '1', '1', '1', '1', '1', 'р']



"Ufeelgood" Куркума молотая 0,2 кг
brand: ufeelgood
good: куркума
['ufeelgood', 'куркума', 'молотая', '1', '1']



Хлопья Овсяные Ясно солнышко 500г/350г в ассортименте
brand: ясно солнышко
good: хлопья
['хлопья', 'овсяные', 'ясно', 'солнышко', '1', '1', 'в', 'ассортименте']



Электронный Персональный Испаритель HQD MAXIM  в ассортименте 400 зат.
brand: hqd
good: испаритель
['электронный', 'персональный', 'испаритель', 'hqd', 'maxim', 'в', 'ассортименте', '1', 'зат']



МИЛКИС 0,25л ж/б персик
brand: милкис
['милкис', '1', '1', 'ж', 'б', 'персик']



Шоколад Merci Storck мол.цельн.лесн.орех 100г
brand: merci
good: шоколад
['шоколад', 'merci', 'storck', 'мол', 'цельн

Brg-BM1260 Точилка механическая Berlingo 2 в 1, цвет металлик, п
brand: berlingo
good: точилка
['brg', 'bm', '1', 'точилка', 'механическая', 'berlingo', '1', 'в', '1', 'цвет', 'металлик', 'п']



Донат с черникой
good: донат
['донат', 'с', 'черникой']



Картон Белый Щенок А4 10л/10цв Хатбер
brand: хатбер
good: картон
['картон', 'белый', 'щенок', 'а', '1', '1', '1', 'цв', 'хатбер']



Б18 2б-03 Носки тонкие
good: носки
['б', '1', '1', 'б', '1', 'носки', 'тонкие']



Псило-бальзам гель 1% 20г туба
brand: псило-бальзам
good: гель
['псило', 'бальзам', 'гель', '1', '1', 'туба']



Масленка 180*95*65мм арт.4312181 шт
good: масленка
['масленка', '1', '1', '1', 'арт', '1']



Бальзам энергия и эмоции- объем, сила, дисциплина волос 1л INDIGO
brand: indigo
good: бальзам
['бальзам', 'энергия', 'и', 'эмоции', 'объем', 'сила', 'дисциплина', 'волос', '1', 'indigo']



Торт фруктовый со сливками вес.
good: торт
['торт', 'фруктовый', 'со', 'сливками', 'вес']



Кекс творожный 60гр
good: кекс
['кекс',

Щетка по металлу 5-рядная пласт.ручка BARTEX
brand: bartex
good: щетка
['щетка', 'по', 'металлу', '1', 'рядная', 'пласт', 'ручка', 'bartex']



швабра с распыл. КН2629
good: швабра
['швабра', 'с', 'распыл', 'кн', '1']



Кума Торронтес Органик вино столовое бел
brand: кума
good: вино
['кума', 'торронтес', 'органик', 'вино', 'столовое', 'бел']



губка банная Неженка уп/25шт (42*12*3см поролон/полиэстер/полиамид)
brand: неженка
good: губка
['губка', 'банная', 'неженка', '1', '1', '1', '1', 'см', 'поролон', 'полиэстер', 'полиамид']



Паста из морепродуктов в ас-те 150г Санта Бремор
brand: санта бремор
good: паста
['паста', 'из', 'морепродуктов', 'в', 'ас', 'те', '1', 'санта', 'бремор']



1) 2864B-99X-38 ТУФЛИ ЖЕНСКИЕ
good: туфли
['1', '1', 'b', '1', 'x', '1', 'туфли', 'женские']



кеды BUF 16301211 бел 37
good: кеды
['кеды', 'buf', '1', 'бел', '1']



_Чай NESTEA черный манго-ананас  0,5л
brand: nestea
good: чай
['_чай', 'nestea', 'черный', 'манго', 'ананас', '1', '1']



Комбинезон B

0% mеpсер изо ванный хлопoк   50 г №014 персик oвый Ар тикул 987992752
good: хлопок
['1', 'мерсер', 'изо', 'ванный', 'хлопок', '1', '1', 'персик', 'овый', 'ар', 'тикул', '1']



ПОДСТАВКА ПОД КОЛЕНИ ДЛЯ РАБОТЫ В САДУ
good: подставка
['подставка', 'под', 'колени', 'для', 'работы', 'в', 'саду']



2. б/х_sc john._глейд 300_океанский оазис (669109)
brand: glade
['1', 'б', 'x_sc', 'john', '_глейд', '1_океанский', 'оазис', '1']



Фуфайка BKT003969 трикотаж белый 10-12л/152
good: фуфайка
['фуфайка', 'bkt', '1', 'трикотаж', 'белый', '1', '1', '1']



Горбуша-палочки сол-суш
good: горбуша
['горбуша', 'палочки', 'сол', 'суш']



Светильник Ecola GX53 H4 Square open edge квадратный Белый с открытым краем 106x41 FW53N4ECB
brand: ecola
good: светильник
['светильник', 'ecola', 'gx', '1', 'h', '1', 'square', 'open', 'edge', 'квадратный', 'белый', 'с', 'открытым', 'краем', '1', 'x', '1', 'fw', '1', 'n', '1', 'ecb']



22252 Конс.овощ Оливки с семгой Солер ж/б 280гр
brand: солер
good: оливки
['1', 'к

...

Салфетки влажные Акватория 15шт/уп  в ассорт. Ы
brand: акватория
good: салфетки
['салфетки', 'влажные', 'акватория', '1', 'в', 'ассорт', 'ы']



1/1 Канефрон н n60 драже
brand: канефрон
good: драже
['1', '1', 'канефрон', 'н', 'n', '1', 'драже']



Сырок творожный глаз. "Вкуснотеево" 40гр Ванилин 23%
brand: вкуснотеево
good: сырок
['сырок', 'творожный', 'глаз', 'вкуснотеево', '1', 'ванилин', '1']



UNIO угол компрессионный нр, 20х3/4"
brand: unio
good: угол
['unio', 'угол', 'компрессионный', 'нр', '1', 'х', '1', '1']



Творог Мама Лама с персиком и грушей 3,8% для детей старше 3-х лет 100г
brand: мама лама
good: творог
['творог', 'мама', 'лама', 'с', 'персиком', 'и', 'грушей', '1', '1', 'для', 'детей', 'старше', '1', 'х', 'лет', '1']



т/бумага 'Мягкий знак' 2-х сл. 4 рулона комф. ассорт. (24)
brand: мягкий знак
good: бумага
['т', 'бумага', 'мягкий', 'знак', '1', 'х', 'сл', '1', 'рулона', 'комф', 'ассорт', '1']



Хлебцы"Бейкер Хаус"розмарин/чеснок
brand: baker house
good: хлебцы
['х

40610 Берет Noryalli (Мульти, ONE SIZE)
brand: noryalli
good: берет
['1', 'берет', 'noryalli', 'мульти', 'one', 'size']



Пакет с прорезанной ручкой (цветной)
good: пакет
['пакет', 'с', 'прорезанной', 'ручкой', 'цветной']



Домик в деревне 950 гр 6 % шт
brand: домик в деревне
['домик', 'в', 'деревне', '1', '1']



БЗМЖ Молоко Простоквашино У\пастериз 3,2% 950 мл.
brand: простоквашино
good: молоко
['бзмж', 'молоко', 'простоквашино', 'у', 'пастериз', '1', '1', '1']



КизК Молоко 2.7 % 900 мл
good: молоко
['кизк', 'молоко', '1', '1', '1']



ПЕЧЕНЬЕ СДОБНОЕ 600Г
good: печенье
['печенье', 'сдобное', '1']



Вода Кубай негаз. спорт 0,5л пэт
brand: кубай
good: вода
['вода', 'кубай', 'негаз', 'спорт', '1', '1', 'пэт']



Клей ПВА 85г лу супер 18с1189-08/00085/193888
good: клей
['клей', 'пва', '1', 'лу', 'супер', '1', 'с', '1', '1', '1', '1']



3.2) 09748 БОЧКАРИ. ВайсБерг Пшеничное, светлое, н/ф, пл. 12%, а
brand: weiss berg
['1', '1', '1', 'бочкари', 'вайсберг', 'пшеничное', 'светлое', '


[M] Кроссовки PUMA LM087776410 m0bh.oD-pFtlT
brand: puma
good: кроссовки
['m', 'кроссовки', 'puma', 'lm', '1', 'mobh', 'o', 'd', 'p', 'ftl', 't']



Dorothy Perkins 67496713 Платье 44 черный
brand: dorothy perkins
good: платье
['dorothy', 'perkins', '1', 'платье', '1', 'черный']



859216 Хаб GINZZU GR-487UAB 1 шт.
brand: ginzzu
good: хаб
['1', 'хаб', 'ginzzu', 'gr', '1', 'uab', '1']



БатончикO ZERA 47г.
brand: o'zera
good: батончик
['батончико', 'zera', '1']



2) 7326I-01X-S ЮБКА ЖЕНСКАЯ
good: юбка
['1', '1', 'i', '1', 'x', 's', 'юбка', 'женская']



Сигареты PARLIAMENT Carat 260 мрц.
brand: parliament
good: сигареты
['сигареты', 'parliament', 'carat', '1', 'мрц']



СВИНЫЕ РЁБРА к/в
good: ребра
['свиные', 'рёбра', 'к', 'в']



6235 Дет. Шорты Nukutavake (синий) (10)
brand: nukutavake
good: шорты
['1', 'дет', 'шорты', 'nukutavake', 'синий', '1']



1.Пижама с длинным рукавом W10106Z8 8683108082776
good: пижама
['1', 'пижама', 'с', 'длинным', 'рукавом', 'w', '1', 'z', '1', '1']





Шапка Prikinder LM094650187
brand: prikinder
good: шапка
['шапка', 'prikinder', 'lm', '1']



2201436005067 Печенье Лимончик, кг
good: печенье
['1', 'печенье', 'лимончик']



Светильник GX53 H4 Квадрат плоский Белый Ecola шт
brand: ecola
good: светильник
['светильник', 'gx', '1', 'h', '1', 'квадрат', 'плоский', 'белый', 'ecola']



30. 00004902 Муфта бронза 1/2" VIEGA
brand: viega
good: муфта
['1', '1', 'муфта', 'бронза', '1', '1', 'viega']



Дюбель-гвоздь 6*50мм борт KEW
brand: kew
good: дюбель-гвоздь
['дюбель', 'гвоздь', '1', '1', 'борт', 'kew']



Патрон 12/70 (Главпатрон) 32г (дробь №3)
brand: главпатрон
good: патрон
['патрон', '1', '1', 'главпатрон', '1', 'дробь', '1']



Сосиски Филейные ц/о /Останкино/ \39
brand: останкино
good: сосиски
['сосиски', 'филейные', 'ц', 'о', 'останкино', '1']



шприц 20мл (шт) (1 x 15)
good: шприц
['шприц', '1', '1', 'x', '1']



2. J.Maki LOOK UP Кондиционер для волос /300
brand: j.maki
good: кондиционер
['1', 'j', 'maki', 'look', 'up', 'кондицион

Трос ДИНАМИЧЕСКИЙ РЫВКОВЫЙ А2ДМ буксировочный 12тн. 6м. 75 мм. Сумка
good: трос
['трос', 'динамический', 'рывковый', 'а', '1', 'дм', 'буксировочный', '1', 'тн', '1', 'м', '1', 'сумка']



Маргарита 40 см тесто пышное
good: товара нет
['маргарита', '1', 'см', 'тесто', 'пышное']



Сырок глазированный Варёная Сгущёнка 40г (Кейко)
brand: keiko
good: сырок
['сырок', 'глазированный', 'варёная', 'сгущёнка', '1', 'кейко']



ЧАЙ ETRE ЗЕЛ 100ГР МОЛОЧНЫЙ УЛУН
brand: etre
good: чай
['чай', 'etre', 'зел', '1', 'молочный', 'улун']



Поддон MB Co №5 мишки smail 24*34*11
brand: smail
good: поддон
['поддон', 'mb', 'co', '1', 'мишки', 'smail', '1', '1', '1']



Кекс Столичный с изюмом     0.272кг*155.00 
good: кекс
['кекс', 'столичный', 'с', 'изюмом', '1', '1', '1', '1']



Вода "Саирме" с/г 500мл
brand: sairme
good: вода
['вода', 'саирме', 'с', '1']



Моя Семя . 0.175л и ассортим
brand: моя семья
['моя', 'семя', '1', '1', 'и', 'ассортим']



Рулет бисквитн.Яшкино клубничный со слив
brand: яшкино
go

In [29]:
# baseline:
#     good:  0.849
#     brand: 0.57
        
# hard_preprocc:
#     good:  0.919689
#     brand: 0.694089

# hard_preprocc + brand renaming
#     good:  0.919689
#     brand: 0.695180

# hard_preprocc + winston lipton ... brand renaming
#     good:  0.919689
#     brand: 0.84692

In [30]:
np.mean(good_founded_list)

0.9196890120342418

In [31]:
np.mean(brand_founded_list)

0.8477720521370112

In [32]:
%%time
names["tokens"] = names["name"].apply(preprocess_text)
names

CPU times: user 59.4 s, sys: 794 ms, total: 1min
Wall time: 1min


name  id  \
0                  Petmax Бантик леопард с красн розой 2шт NaN   
1                         87191 Бусы для елки шарики_87191 NaN   
2                       Футболка Piazza Italia WR011446881 NaN   
3           7) YI572-03X-ONE ЗАКОЛКА ДЛЯ ВОЛОС ДЛЯ ДЕВОЧКИ NaN   
4                                        Одежда (вес) 1500 NaN   
...                                                    ...  ..   
1029995              F-2296  Спонж д/макияжа фигурный (шт) NaN   
1029996               4 5702737510597 69.88 Дифф/Arom/1601 NaN   
1029997  Матрас надувной 540*74см Tropical Bird запл.д/... NaN   
1029998  пододеяльник СТМ Страйп 3-сп, размер: 796х185с... NaN   
1029999  Пакет ламинированный вертикальный ?Чудесных мг... NaN   

                                                    tokens  
0            [petmax, бантик, леопард, с, красн, розой, 1]  
1                           [1, бусы, для, елки, шарики_1]  
2                        [футболка, piazza, italia, wr, 1]  
3        [1, yi, 1, 1, x, one, заколка, для, волос, для...  
4                                         [одежда, вес, 1]  
...                                                    ...  
1029995              [f, 1, спонж, для, макияжа, фигурный]  
1029996                        [1, 1, 1, 1, дифф, arom, 1]  
1029997  [матрас, надувной, 1, 1, см, tropical, bird, з...  
1029998  [пододеяльник, стм, страйп, 1, сп, размер, 1, ...  
1029999  [пакет, ламинированный, вертикальный, чудесных...  

[1030000 rows x 3 columns]

In [33]:
names.to_csv('data/preprocc_names.csv', index=False)

Обученные векторы положим в файл `fasttext.model` для использования в моделях

In [34]:
%%time
FastText(names["tokens"], vector_size=512, window=5, min_count=5, epochs=20).save("fasttext_models/fasttext_512_hardpreprocc_renamed_fitted.model")

CPU times: user 28min 18s, sys: 2min 11s, total: 30min 29s
Wall time: 11min 33s
